In [16]:
# MWE Hyperelasticity ##

In [17]:
# geometric non-linear elasticity with Neo-Hooke hyperelastic material
#
# featuring automatic differentiation in SymbolicEnergy
#

import netgen.geom2d as geom2d
from ngsolve import *
import time

geo = geom2d.SplineGeometry()
pnums = [ geo.AddPoint (x,y,maxh=0.01) for x,y in [(0,0), (1,0), (1,0.1), (0,0.1)] ]
for p1,p2,bc in [(0,1,"bot"), (1,2,"right"), (2,3,"top"), (3,0,"left")]:
     geo.Append(["line", pnums[p1], pnums[p2]], bc=bc)
mesh = Mesh(geo.GenerateMesh(maxh=0.005))


E, nu = 210, 0.2
mu  = E / 2 / (1+nu)
lam = E * nu / ((1+nu)*(1-2*nu))

fes = H1(mesh, order=1, dirichlet="left", dim=mesh.dim)

u, u_test = fes.TnT()

force = CoefficientFunction( (0,1/2) )

I = Id(mesh.dim)

def F(u):
    return I + Grad(u)


def Pow(a, b):
    return a**b  # exp (log(a)*b)
  
def NeoHooke (F):
    C = F.trans * F
    return 0.5 * mu * (Trace(C-I) + 2*mu/lam * Pow(Det(C),-lam/2/mu) - 1)


factor = Parameter(1)

In [18]:
## Variant I: Solution using AssembleLinearization ##

a = BilinearForm(fes, symmetric=True)
a += Variation (NeoHooke(F(u)).Compile()*dx)
a += Variation ((-factor * InnerProduct(force,u) ).Compile()*dx)


gfu = GridFunction(fes)
gfu.vec[:] = 0

res = gfu.vec.CreateVector()
w = gfu.vec.CreateVector()



tic = time.perf_counter()

for loadstep in range(1):
    
    print ("loadstep", loadstep)
    factor.Set (loadstep+1)
    
    for it in range(10):
        print ("Newton iteration", it)
        a.Apply(gfu.vec, res)
        a.AssembleLinearization(gfu.vec)
        inv = a.mat.Inverse(fes.FreeDofs() ) 
        w.data = inv*res
        print ("err^2 = ", InnerProduct (w,res))
        gfu.vec.data -= w 
        
        
toc = time.perf_counter()
print("----------------")
print(f"Time for solution: {toc - tic:0.4f} seconds")

loadstep 0
Newton iteration 0
err^2 =  0.006928531215097386
Newton iteration 1
err^2 =  0.307774491109197
Newton iteration 2
err^2 =  0.002990896190524022
Newton iteration 3
err^2 =  3.523184442211581e-05
Newton iteration 4
err^2 =  1.5179998627570816e-07
Newton iteration 5
err^2 =  4.4911265910827375e-11
Newton iteration 6
err^2 =  1.8277400304335765e-17
Newton iteration 7
err^2 =  2.574256703568751e-28
Newton iteration 8
err^2 =  2.5372914646492117e-28
Newton iteration 9
err^2 =  2.0035439595379165e-28
----------------
Time for solution: 1.2907 seconds


In [19]:
## Variant II: Linearization via Autodiff & Assemble linear and bilinear forms via Assemble ##

F_gf = F(gfu).MakeVariable()

# stress
PK1 = NeoHooke(F_gf).Diff(F_gf)

L = LinearForm(fes)
L += InnerProduct(PK1, Grad(u_test)).Compile() * dx
L += (-factor * InnerProduct(force,u_test) ).Compile()*dx


# elasticity tensor
AA = PK1.Diff(F_gf).Reshape((F_gf.dim, F_gf.dim))

# reshape test and trial strians
delta_F = Grad(u_test).Reshape((F_gf.dim, ))
Delta_F = Grad(u).Reshape((F_gf.dim, ))

a = BilinearForm(fes, symmetric=True)

# Bilinearform
a += InnerProduct(delta_F, AA * Delta_F).Compile() * dx



w = gfu.vec.CreateVector()


gfu.vec[:] = 0

tic = time.perf_counter()


for loadstep in range(1):
    
    print ("loadstep", loadstep)
    factor.Set (loadstep+1)
    
    for it in range(10):
        print ("Newton iteration", it)
        a.Assemble()
        L.Assemble()
        inv = a.mat.Inverse(fes.FreeDofs()) 
        w.data = inv*L.vec
        print ("err^2 = ", InnerProduct (w,L.vec))
        gfu.vec.data -= w 
        
toc = time.perf_counter()
print("----------------")
print(f"Time for solution: {toc - tic:0.4f} seconds")        

loadstep 0
Newton iteration 0
err^2 =  0.006928531215232013
Newton iteration 1
err^2 =  0.3077744911330631
Newton iteration 2
err^2 =  0.0029908961909882125
Newton iteration 3
err^2 =  3.5231844484739314e-05
Newton iteration 4
err^2 =  1.5179998681301478e-07
Newton iteration 5
err^2 =  4.491126626072357e-11
Newton iteration 6
err^2 =  1.827740050699693e-17
Newton iteration 7
err^2 =  2.4317389703281575e-28
Newton iteration 8
err^2 =  2.5123238852748544e-28
Newton iteration 9
err^2 =  2.4797108498932484e-28
----------------
Time for solution: 4.5667 seconds
